In [1]:
import geemap
import ee
# ee.Authenticate()
ee.Initialize()

In [2]:
import json

In [3]:
positives_file = r"G:\.shortcut-targets-by-id\1F5TKMAk_9oNKo13HfwksVmLXmT-4Wy2n\WBS_Project\Database\true_positive_points.geojson" # path to geojson file containing locations of known, unexploited PCDs
with open(positives_file) as data_file:
  p= json.load(data_file)

In [47]:
p['features'][0]

{'type': 'Feature',
 'properties': {'GMRAP_ID': 216,
  'NAME': 'Acandi',
  'DEP_TYPE': 'Porphyry copper',
  'DEP_SUBTYP': 'NA',
  'DEV_STATUS': 'Prospect',
  'URL': 'http://mrdata.usgs.gov/sir20105090z/show-sir20105090z.php?gmrap_id=216'},
 'geometry': {'type': 'Point',
  'coordinates': [-77.32138888899993, 8.487777778000066]}}

In [48]:
p['features'][0]['geometry']['coordinates']

[-77.32138888899993, 8.487777778000066]

In [49]:
coords = p['features'][0]['geometry']['coordinates']

In [50]:
projection = ee.ImageCollection("ASTER/AST_L1T_003").filterBounds(ee.Geometry.Point(coords = coords)).first().select('B3N').projection()
projection.getInfo()

{'type': 'Projection',
 'crs': 'EPSG:32618',
 'transform': [15, 0, 236603, 0, -15, 989468]}

In [51]:
projection.getInfo()

{'type': 'Projection',
 'crs': 'EPSG:32618',
 'transform': [15, 0, 236603, 0, -15, 989468]}

In [52]:
def create_box(coords, distance = 3000):
  point = ee.Geometry.Point(coords)
  proj = ee.ImageCollection("ASTER/AST_L1T_003").filterBounds(ee.Geometry.Point(coords = coords)).first().select('B01').projection()
  proj = proj.atScale(1) # This is necessary because the units of the projections are not necessarily a single meter. This scales all projections so that the unit is 1 m.
  buffer = point.buffer(distance, proj = proj)
  bbox = buffer.bounds(proj = proj)
  return bbox

In [53]:
test_bbox = create_box(coords)
test_bbox

ee.Geometry({
  "functionInvocationValue": {
    "functionName": "Geometry.bounds",
    "arguments": {
      "geometry": {
        "functionInvocationValue": {
          "functionName": "Geometry.buffer",
          "arguments": {
            "distance": {
              "constantValue": 3000
            },
            "geometry": {
              "functionInvocationValue": {
                "functionName": "GeometryConstructors.Point",
                "arguments": {
                  "coordinates": {
                    "constantValue": [
                      -77.32138888899993,
                      8.487777778000066
                    ]
                  }
                }
              }
            },
            "proj": {
              "functionInvocationValue": {
                "functionName": "Projection",
                "arguments": {
                  "crs": {
                    "functionInvocationValue": {
                      "functionName": "Projection.atScale",
                      "arguments": {
                        "meters": {
                          "constantValue": 1
                        },
                        "projection": {
                          "functionInvocationValue": {
                            "functionName": "Projection",
                            "arguments": {
                              "crs": {
                                "functionInvocationValue": {
                                  "functionName": "Image.projection",
                                  "arguments": {
                                    "image": {
                                      "functionInvocationValue": {
                                        "functionName": "Image.select",
                                        "arguments": {
                                          "bandSelectors": {
                                            "constantValue": [
                                              "B01"
                                            ]
                                          },
                                          "input": {
                                            "functionInvocationValue": {
                                              "functionName": "Collection.first",
                                              "arguments": {
                                                "collection": {
                                                  "functionInvocationValue": {
                                                    "functionName": "Collection.filter",
                                                    "arguments": {
                                                      "collection": {
                                                        "functionInvocationValue": {
                                                          "functionName": "ImageCollection.load",
                                                          "arguments": {
                                                            "id": {
                                                              "constantValue": "ASTER/AST_L1T_003"
                                                            }
                                                          }
                                                        }
                                                      },
                                                      "filter": {
                                                        "functionInvocationValue": {
                                                          "functionName": "Filter.intersects",
                                                          "arguments": {
                                                            "leftField": {
                                                              "constantValue": ".all"
                                                            },
                                                            "rightValue": {
                     

In [54]:
point = ee.Geometry.Point(coords)
proj = ee.ImageCollection("ASTER/AST_L1T_003").filterBounds(ee.Geometry.Point(coords = coords)).first().select('B01').projection()
buffer = point.buffer(distance = 3000, proj = proj)

In [55]:
map = geemap.Map()
map.addLayer(point)
map.addLayer(buffer)
map.addLayer(test_bbox)
map.center_object(point, zoom = 5)
map

KeyboardInterrupt: 

In [ ]:
projection.nominalScale().getInfo()

15

gonna try to calculate bboxes for all pcd points at once as a feature collection

In [ ]:
pcds_ee = geemap.geojson_to_ee(positives_file)

In [ ]:
map2 = geemap.Map()
map2.addLayer(pcds_ee)
map2

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [ ]:
type(pcds_ee)

ee.featurecollection.FeatureCollection

In [ ]:
type(pcds_ee.first().geometry())

ee.geometry.Geometry

In [ ]:
def box_from_feature(feature):
  point = feature.geometry()
  proj = ee.ImageCollection("ASTER/AST_L1T_003").filterBounds(ee.Geometry.Point(coords = coords)).first().select('B01').projection()
  proj = proj.atScale(1) # This is necessary because the units of the projections are not necessarily a single meter. This scales all projections so that the unit is 1 m.
  buffer = point.buffer(distance = 3000, proj = proj)
  bbox = buffer.bounds(proj = proj)
  bbox = ee.Feature(bbox)
  return bbox    

In [ ]:
test_box_from_feature = box_from_feature(pcds_ee.first())
test_box_from_feature

In [ ]:
pcd_boxes = pcds_ee.map(box_from_feature)

In [ ]:
pcd_boxes.size()

In [ ]:
pcd_boxes.first().geometry()

ee.Geometry({
  "functionInvocationValue": {
    "functionName": "Element.geometry",
    "arguments": {
      "feature": {
        "functionInvocationValue": {
          "functionName": "Collection.first",
          "arguments": {
            "collection": {
              "functionInvocationValue": {
                "functionName": "Collection.map",
                "arguments": {
                  "baseAlgorithm": {
                    "functionDefinitionValue": {
                      "argumentNames": [
                        "_MAPPING_VAR_0_0"
                      ],
                      "body": {
                        "functionInvocationValue": {
                          "functionName": "Feature",
                          "arguments": {
                            "geometry": {
                              "functionInvocationValue": {
                                "functionName": "Geometry.bounds",
                                "arguments": {
                                  "geometry": {
                                    "functionInvocationValue": {
                                      "functionName": "Geometry.buffer",
                                      "arguments": {
                                        "distance": {
                                          "constantValue": 3000
                                        },
                                        "geometry": {
                                          "functionInvocationValue": {
                                            "functionName": "Feature.geometry",
                                            "arguments": {
                                              "feature": {
                                                "argumentReference": "_MAPPING_VAR_0_0"
                                              }
                                            }
                                          }
                                        },
                                        "proj": {
                                          "functionInvocationValue": {
                                            "functionName": "Projection",
                                            "arguments": {
                                              "crs": {
                                                "functionInvocationValue": {
                                                  "functionName": "Projection.atScale",
                                                  "arguments": {
                                                    "meters": {
                                                      "constantValue": 1
                                                    },
                                                    "projection": {
                                                      "functionInvocationValue": {
                                                        "functionName": "Projection",
                                                        "arguments": {
                                                          "crs": {
                                                            "functionInvocationValue": {
                                                              "functionName": "Image.projection",
                                                              "arguments": {
                                                                "image": {
                                                                  "functionInvocationValue": {
                                                                    "functionName": "Image.select",
                                                                    "arguments": {
                                                                      "bandSelectors": {
                                                                        "constantValue": [
                                                                          "B01"
                                                     

In [ ]:
geemap.ee_export_vector(pcd_boxes, "test_bboxes/pcd_boxes.geojson")

Generating URL ...
Please wait ...
Data downloaded to p:\Eli\Mining_for_the_Future\porphyry-copper-deposit-prediction\test_bboxes\pcd_boxes.geojson


In [ ]:
map3 = geemap.Map()
map3.addLayer(pcd_boxes)
map3.centerObject(point, zoom = 7)

In [ ]:
map3

Map(center=[8.487777778000066, -77.32138888899993], controls=(WidgetControl(options=['position', 'transparent_…

That did not work because it assigned the same projection to everything. Need to iterate through each point in the json and export each box on its own. Gonna select 100 at random to save time.

In [ ]:
import random

In [ ]:
test_pcd_samp = random.choices(p['features'], k = 100)

In [ ]:
def create_box(coords, distance = 3000):
  point = ee.Geometry.Point(coords)
  proj = ee.ImageCollection("ASTER/AST_L1T_003").filterBounds(ee.Geometry.Point(coords = coords)).first().select('B01').projection()
  proj = proj.atScale(1) # This is necessary because the units of the projections are not necessarily a single meter. This scales all projections so that the unit is 1 m.
  buffer = point.buffer(distance, proj = proj)
  bbox = buffer.bounds(proj = proj)
  return bbox

In [ ]:
test_pcd_samp[0]

{'type': 'Feature',
 'properties': {'GMRAP_ID': 97,
  'NAME': 'Sunnyside',
  'DEP_TYPE': 'Porphyry copper',
  'DEP_SUBTYP': 'NA',
  'DEV_STATUS': 'Prospect',
  'URL': 'http://mrdata.usgs.gov/sir20105090z/show-sir20105090z.php?gmrap_id=97'},
 'geometry': {'type': 'Point',
  'coordinates': [-110.74611111099995, 31.451111111000046]}}

In [ ]:
test_pcd_samp[0]['properties']['GMRAP_ID']

97

In [ ]:
'pcd_' + str(test_pcd_samp[0]['properties']['GMRAP_ID']) + '.geojson'

'pcd_97.geojson'

In [ ]:
for samp in test_pcd_samp:
    box = ee.FeatureCollection(create_box(samp['geometry']['coordinates']))
    name = 'pcd_' + str(samp['properties']['GMRAP_ID']) + '.geojson'
    file = r'test_bboxes/' + name
    geemap.ee_export_vector(box, name)

Generating URL ...
Please wait ...
Data downloaded to p:\Eli\Mining_for_the_Future\porphyry-copper-deposit-prediction\pcd_97.geojson
Generating URL ...
Please wait ...
Data downloaded to p:\Eli\Mining_for_the_Future\porphyry-copper-deposit-prediction\pcd_4046.geojson
Generating URL ...
Please wait ...
Data downloaded to p:\Eli\Mining_for_the_Future\porphyry-copper-deposit-prediction\pcd_9161.geojson
Generating URL ...
Please wait ...
Data downloaded to p:\Eli\Mining_for_the_Future\porphyry-copper-deposit-prediction\pcd_321.geojson
Generating URL ...
Please wait ...
Data downloaded to p:\Eli\Mining_for_the_Future\porphyry-copper-deposit-prediction\pcd_7011.geojson
Generating URL ...
Please wait ...
Data downloaded to p:\Eli\Mining_for_the_Future\porphyry-copper-deposit-prediction\pcd_7081.geojson
Generating URL ...
Please wait ...
Data downloaded to p:\Eli\Mining_for_the_Future\porphyry-copper-deposit-prediction\pcd_9337.geojson
Generating URL ...
Please wait ...
Data downloaded to p:\E

This generated a bunch of geojson files. When I imported them into ArcGIS, though, the JSON to feature tool projected everything into WGS 84, which makes area calculations basically useless

gonna try to calculate area here using google earth engine tools

In [ ]:
test_pcd_samp

[{'type': 'Feature',
  'properties': {'GMRAP_ID': 97,
   'NAME': 'Sunnyside',
   'DEP_TYPE': 'Porphyry copper',
   'DEP_SUBTYP': 'NA',
   'DEV_STATUS': 'Prospect',
   'URL': 'http://mrdata.usgs.gov/sir20105090z/show-sir20105090z.php?gmrap_id=97'},
  'geometry': {'type': 'Point',
   'coordinates': [-110.74611111099995, 31.451111111000046]}},
 {'type': 'Feature',
  'properties': {'GMRAP_ID': 4046,
   'NAME': 'Cadia Far East',
   'DEP_TYPE': 'Porphyry copper',
   'DEP_SUBTYP': 'Cu-Au',
   'DEV_STATUS': 'Prospect',
   'URL': 'http://mrdata.usgs.gov/sir20105090z/show-sir20105090z.php?gmrap_id=4046'},
  'geometry': {'type': 'Point', 'coordinates': [149.0156, -33.4605]}},
 {'type': 'Feature',
  'properties': {'GMRAP_ID': 9161,
   'NAME': 'Reko Diq H27',
   'DEP_TYPE': 'Porphyry copper',
   'DEP_SUBTYP': 'NA',
   'DEV_STATUS': 'Prospect',
   'URL': 'http://mrdata.usgs.gov/sir20105090z/show-sir20105090z.php?gmrap_id=9161'},
  'geometry': {'type': 'Point', 'coordinates': [62.0959, 29.0932]}},
 {

In [ ]:
test_bbox.area(maxError = 1).getInfo()

36121582.736657165

In [4]:
import pandas as pd

In [ ]:
sample_areas = pd.DataFrame({"id": [], "area": [], "deviation_from_36sqkm":[]})


In [ ]:

for samp in test_pcd_samp:
    id  = samp['properties']['GMRAP_ID']
    box = ee.Feature(create_box(samp['geometry']['coordinates']))
    area = (box.area(maxError = 1).getInfo())
    deviation = abs(area - 36000000)/36000000
    sample_areas = pd.concat([sample_areas,
                              pd.DataFrame({
                                  "id": [id],
                                  "area": [area],
                                  "deviation_from_36sqkm": [deviation]
                              }) ])

In [ ]:
sample_areas.sort_values(by = "deviation_from_36sqkm", ascending = False)

id          area  deviation_from_36sqkm
0   3348.0  3.048737e+07               0.153129
0   3358.0  3.063904e+07               0.148916
0     97.0  3.064246e+07               0.148821
0    175.0  3.075252e+07               0.145763
0   3018.0  3.083906e+07               0.143359
..     ...           ...                    ...
0   9039.0  3.598735e+07               0.000351
0   9238.0  3.598750e+07               0.000347
0   4046.0  3.601226e+07               0.000340
0   9249.0  3.599365e+07               0.000176
0   9370.0  3.599755e+07               0.000068

[100 rows x 3 columns]

In [ ]:
test_pcd_samp_df = pd.DataFrame(pd.json_normalize(test_pcd_samp))

In [ ]:
test_pcd_samp_df.head()

type  properties.GMRAP_ID  properties.NAME properties.DEP_TYPE  \
0  Feature                   97        Sunnyside     Porphyry copper   
1  Feature                 4046   Cadia Far East     Porphyry copper   
2  Feature                 9161     Reko Diq H27     Porphyry copper   
3  Feature                  321  Bajo El Durazno     Porphyry copper   
4  Feature                 7011          Bonakan     Porphyry copper   

  properties.DEP_SUBTYP properties.DEV_STATUS  \
0                    NA              Prospect   
1                 Cu-Au              Prospect   
2                    NA              Prospect   
3                    NA              Prospect   
4                    NA              Prospect   

                                      properties.URL geometry.type  \
0  http://mrdata.usgs.gov/sir20105090z/show-sir20...         Point   
1  http://mrdata.usgs.gov/sir20105090z/show-sir20...         Point   
2  http://mrdata.usgs.gov/sir20105090z/show-sir20...         Point   
3  http://mrdata.usgs.gov/sir20105090z/show-sir20...         Point   
4  http://mrdata.usgs.gov/sir20105090z/show-sir20...         Point   

                        geometry.coordinates  
0  [-110.74611111099995, 31.451111111000046]  
1                       [149.0156, -33.4605]  
2                         [62.0959, 29.0932]  
3  [-66.56666666699994, -27.283333332999973]  
4                      [124.18333, 10.11666]

In [ ]:
test_pcd_samp_df.loc[test_pcd_samp_df['properties.GMRAP_ID'] == 96, 'geometry.coordinates']

Series([], Name: geometry.coordinates, dtype: object)

In [ ]:
pcd_96_coords = test_pcd_samp_df.loc[test_pcd_samp_df['properties.GMRAP_ID'] == 96, 'geometry.coordinates'][67]

KeyError: 67

In [ ]:
pcd_96_coords

[-110.72, 31.49]

In [ ]:
def create_box(coords, distance = 3000):
  point = ee.Geometry.Point(coords)
  proj = ee.ImageCollection("ASTER/AST_L1T_003").filterBounds(ee.Geometry.Point(coords = coords)).first().select('B01').projection()
  proj = proj.atScale(1) # This is necessary because the units of the projections are not necessarily a single meter. This scales all projections so that the unit is 1 m.
  buffer = point.buffer(distance, proj = proj)
  bbox = buffer.bounds(proj = proj)
  return bbox

In [ ]:
create_box(pcd_96_coords)

ee.Geometry({
  "functionInvocationValue": {
    "functionName": "Geometry.bounds",
    "arguments": {
      "geometry": {
        "functionInvocationValue": {
          "functionName": "Geometry.buffer",
          "arguments": {
            "distance": {
              "constantValue": 3000
            },
            "geometry": {
              "functionInvocationValue": {
                "functionName": "GeometryConstructors.Point",
                "arguments": {
                  "coordinates": {
                    "constantValue": [
                      -110.72,
                      31.49
                    ]
                  }
                }
              }
            },
            "proj": {
              "functionInvocationValue": {
                "functionName": "Projection",
                "arguments": {
                  "crs": {
                    "functionInvocationValue": {
                      "functionName": "Projection.atScale",
                      "arguments": {
                        "meters": {
                          "constantValue": 1
                        },
                        "projection": {
                          "functionInvocationValue": {
                            "functionName": "Projection",
                            "arguments": {
                              "crs": {
                                "functionInvocationValue": {
                                  "functionName": "Image.projection",
                                  "arguments": {
                                    "image": {
                                      "functionInvocationValue": {
                                        "functionName": "Image.select",
                                        "arguments": {
                                          "bandSelectors": {
                                            "constantValue": [
                                              "B01"
                                            ]
                                          },
                                          "input": {
                                            "functionInvocationValue": {
                                              "functionName": "Collection.first",
                                              "arguments": {
                                                "collection": {
                                                  "functionInvocationValue": {
                                                    "functionName": "Collection.filter",
                                                    "arguments": {
                                                      "collection": {
                                                        "functionInvocationValue": {
                                                          "functionName": "ImageCollection.load",
                                                          "arguments": {
                                                            "id": {
                                                              "constantValue": "ASTER/AST_L1T_003"
                                                            }
                                                          }
                                                        }
                                                      },
                                                      "filter": {
                                                        "functionInvocationValue": {
                                                          "functionName": "Filter.intersects",
                                                          "arguments": {
                                                            "leftField": {
                                                              "constantValue": ".all"
                                                            },
                                                            "rightValue": {
                                            

OK, this is important. This means that the band B01 of the first ASTER image that intersects the point is not a reliable carrier of projection information.

I need to get projection information from somewhere else. As recommended by ChatGPT I'll use the pyproj library.

Actually, it seems like the UTM library is probably what I want, so skip to the next markup

In [5]:
import pyproj

In [6]:
def get_utm_zone_epsg_code(coordinates):
    # Check if the input is in the format [Longitude, Latitude]
    if len(coordinates) != 2:
        raise ValueError("Input coordinates should be in the format [Longitude, Latitude].")

    # Extract longitude and latitude from the input
    longitude, latitude = coordinates

    # Create a UTM projection object
    utm = pyproj.Proj(proj="utm", zone=None, ellps="WGS84")

    # Transform the coordinates to UTM
    easting, northing = utm(longitude, latitude)

    # Determine the UTM zone from the easting value
    utm_zone = int((easting + 180) / 6) + 1

    # Determine the EPSG code based on the northern/southern hemisphere
    if latitude >= 0:
        epsg_code = 32600 + utm_zone
    else:
        epsg_code = 32700 + utm_zone

    return epsg_code

# Example usage:
coordinates = [-122.4194, 37.7749]  # San Francisco coordinates [Longitude, Latitude]
#epsg_code = get_utm_zone_epsg_code(coordinates)
print(f"EPSG code for the UTM zone containing the coordinates: {epsg_code}")


NameError: name 'epsg_code' is not defined

In [ ]:
def get_utm_zone_epsg_code(coordinates):
    # Check if the input is in the format [Longitude, Latitude]
    if len(coordinates) != 2:
        raise ValueError("Input coordinates should be in the format [Longitude, Latitude].")

    # Extract longitude and latitude from the input
    longitude, latitude = coordinates

    # Determine the UTM zone based on the longitude value
    utm_zone = int((longitude + 180) / 6) + 1

    # Determine the EPSG code based on the northern/southern hemisphere
    if latitude >= 0:
        epsg_code = 32600 + utm_zone
    else:
        epsg_code = 32700 + utm_zone

    return epsg_code

# Example usage:
coordinates = [-122.4194, 37.7749]  # San Francisco coordinates [Longitude, Latitude]
epsg_code = get_utm_zone_epsg_code(coordinates)
print(f"EPSG code for the UTM zone containing the coordinates: {epsg_code}")

EPSG code for the UTM zone containing the coordinates: 32610


This doesn't account for complex zones near the poles. Check out the bespoke python package [`utm`](https://github.com/Turbo87/utm/tree/master/utm).

The function `from_latlon` and the hidden functions `latlon_to_zone_number` and `latitude_to_zone_letter` will be useful. Just need to figure out how to transform this into EPSG code. The below cell is ChatGPT's attempt

I want to spend the time to make sure I understand all the complexities of the UTM system before I trust this finally

In [7]:
import utm

def get_utm_zone_epsg_code(coordinates):
    # Check if the input is in the format [Longitude, Latitude]
    if len(coordinates) != 2:
        raise ValueError("Input coordinates should be in the format [Longitude, Latitude].")

    # Extract longitude and latitude from the input
    longitude, latitude = coordinates

    # Calculate UTM zone and hemisphere
    utm_zone = utm.latlon_to_zone_number(latitude, longitude)
    # utm_zone, utm_letter = utm.from_latlon(latitude, longitude)[2:]

    # Determine the EPSG code based on the hemisphere
    if latitude >= 0:
        epsg_code = 32600 + utm_zone
    else:
        epsg_code = 32700 + utm_zone

    return 'EPSG:'+str(epsg_code)

# Example usage:
coordinates = [-122.4194, 37.7749]  # San Francisco coordinates [Longitude, Latitude]
epsg_code = get_utm_zone_epsg_code(coordinates)
print(f"EPSG code for the UTM zone containing the coordinates: {epsg_code}")


EPSG code for the UTM zone containing the coordinates: EPSG:32610


In [11]:
p['features']

[{'type': 'Feature',
  'properties': {'GMRAP_ID': 216,
   'NAME': 'Acandi',
   'DEP_TYPE': 'Porphyry copper',
   'DEP_SUBTYP': 'NA',
   'DEV_STATUS': 'Prospect',
   'URL': 'http://mrdata.usgs.gov/sir20105090z/show-sir20105090z.php?gmrap_id=216'},
  'geometry': {'type': 'Point',
   'coordinates': [-77.32138888899993, 8.487777778000066]}},
 {'type': 'Feature',
  'properties': {'GMRAP_ID': 266,
   'NAME': 'Alondra',
   'DEP_TYPE': 'Porphyry copper',
   'DEP_SUBTYP': 'NA',
   'DEV_STATUS': 'Prospect',
   'URL': 'http://mrdata.usgs.gov/sir20105090z/show-sir20105090z.php?gmrap_id=266'},
  'geometry': {'type': 'Point',
   'coordinates': [-73.58333333299998, -15.816666666999936]}},
 {'type': 'Feature',
  'properties': {'GMRAP_ID': 635,
   'NAME': 'Alto Dorado',
   'DEP_TYPE': 'Porphyry copper',
   'DEP_SUBTYP': 'NA',
   'DEV_STATUS': 'Occurrence',
   'URL': 'http://mrdata.usgs.gov/sir20105090z/show-sir20105090z.php?gmrap_id=635'},
  'geometry': {'type': 'Point',
   'coordinates': [-78.18333333

In [12]:
import numpy as np

In [14]:
pcd_coords = [[x['geometry']['coordinates'][0], x['geometry']['coordinates'][1]] for x in p['features']]

In [23]:
# check max and min of all pcd coords to make sure they don't fall outside the bounds of UTM
pcd_coords = np.array(pcd_coords)
print(pcd_coords[:,1].min()>= -80)
print(pcd_coords[:,1].max()<= 84)

True
True


In [27]:
ee.Projection(get_utm_zone_epsg_code(p['features'][0]['geometry']['coordinates']))

Ok, lets test out the process of getting projections from coordinates using the UTM package

In [29]:
import random
test_pcd_samp = random.choices(p['features'], k = 100)

In [30]:
def create_box(coords, distance = 3000):
  point = ee.Geometry.Point(coords)
  proj = ee.Projection(get_utm_zone_epsg_code(coords))
  proj = proj.atScale(1) # This is necessary because the units of the projections are not necessarily a single meter. This scales all projections so that the unit is 1 m.
  buffer = point.buffer(distance, proj = proj)
  bbox = buffer.bounds(proj = proj)
  return bbox

In [31]:
sample_areas = pd.DataFrame({"id": [], "area": [], "deviation_from_36sqkm":[]})

In [32]:
for samp in test_pcd_samp:
    id  = samp['properties']['GMRAP_ID']
    box = ee.Feature(create_box(samp['geometry']['coordinates']))
    area = (box.area(maxError = 1).getInfo())
    deviation = abs(area - 36000000)/36000000
    sample_areas = pd.concat([sample_areas,
                              pd.DataFrame({
                                  "id": [id],
                                  "area": [area],
                                  "deviation_from_36sqkm": [deviation]
                              }) ])

In [33]:
sample_areas.sort_values(by = "deviation_from_36sqkm", ascending = False)

id          area  deviation_from_36sqkm
0   3434.0  3.577194e+07               0.006335
0   9985.0  3.578373e+07               0.006008
0   3382.0  3.580098e+07               0.005528
0   3412.0  3.580495e+07               0.005418
0   9996.0  3.581158e+07               0.005234
..     ...           ...                    ...
0   9138.0  3.601195e+07               0.000332
0   9215.0  3.598959e+07               0.000289
0   9374.0  3.599020e+07               0.000272
0   9229.0  3.599198e+07               0.000223
0     55.0  3.599808e+07               0.000053

[100 rows x 3 columns]

In [34]:
pcd_areas = pd.DataFrame({"id": [], "area": [], "deviation_from_36sqkm":[]})

In [35]:
for samp in p['features']:
    id  = samp['properties']['GMRAP_ID']
    box = ee.Feature(create_box(samp['geometry']['coordinates']))
    area = (box.area(maxError = 1).getInfo())
    deviation = abs(area - 36000000)/36000000
    pcd_areas = pd.concat([pcd_areas,
                              pd.DataFrame({
                                  "id": [id],
                                  "area": [area],
                                  "deviation_from_36sqkm": [deviation]
                              }) ])
pcd_areas.sort_values(by = "deviation_from_36sqkm", ascending = False)

id          area  deviation_from_36sqkm
0   7213.0  3.576747e+07               0.006459
0      1.0  3.576879e+07               0.006422
0   3433.0  3.576921e+07               0.006411
0   7214.0  3.577191e+07               0.006336
0   3432.0  3.577191e+07               0.006336
..     ...           ...                    ...
0   4026.0  3.599956e+07               0.000012
0   9352.0  3.600036e+07               0.000010
0    582.0  3.599980e+07               0.000006
0    583.0  3.599982e+07               0.000005
0   9089.0  3.599989e+07               0.000003

[1882 rows x 3 columns]

ok, final test to see if it works running straight from the module

In [1]:
import ee
ee.Initialize()
import geemap
import json

In [3]:
from projected_box import create_box

In [2]:
positives_file = r"G:\.shortcut-targets-by-id\1F5TKMAk_9oNKo13HfwksVmLXmT-4Wy2n\WBS_Project\Database\true_positive_points.geojson" # path to geojson file containing locations of known, unexploited PCDs
with open(positives_file) as data_file:
  p= json.load(data_file)

In [4]:
pcd = p['features'][1056]

In [5]:
coordinates = pcd['geometry']['coordinates']
point = ee.Geometry.Point(coordinates)
box = create_box(coordinates)

In [10]:
box.area(maxError = 1).getInfo()

35914497.219350666

In [7]:
map = geemap.Map()
map.addLayer(point)
map.addLayer(box)
map.centerObject(box, zoom = 12)
map

Map(center=[46.11599991983609, 23.168999682703607], controls=(WidgetControl(options=['position', 'transparent_…

IT WORKS!